# Solving the first problem (4 qubits circuit)
We began by using pennylane to load the qasm circuit and use the default simulator. We then used qml.probs to get the probability distribution. From that, we can look at the index of the highest value of the returned array to figure out the value that we want. we then converted the index number to a binary string. 

In [1]:
import pennylane as qml
import numpy as np
import bluequbit
import json
import os
from dotenv import load_dotenv
from collections import Counter


In [ ]:
# all the libraries we are going to need
%pip install python-dotenv
%pip install bluequbit
%pip install circuit-knitting-toolbox
%pip install pennylane-qiskit


[notice] A new release of pip is available: 24.2 -> 25.0.1
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.2 -> 25.0.1
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.2 -> 25.0.1
[notice] To update, run: python.exe -m pip install --upgrade pip


  Using cached qiskit-1.2.4-cp38-abi3-win_amd64.whl.metadata (13 kB)
Using cached qiskit-1.2.4-cp38-abi3-win_amd64.whl (4.6 MB)
  Attempting uninstall: qiskit
    Found existing installation: qiskit 1.4.2
    Uninstalling qiskit-1.4.2:
      Successfully uninstalled qiskit-1.4.2
Note: you may need to restart the kernel to use updated packages.


ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
qiskit-addon-cutting 0.10.0 requires qiskit<3,>=1.3.1, but you have qiskit 1.2.4 which is incompatible.

[notice] A new release of pip is available: 24.2 -> 25.0.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
qasm_path = "circuit_qasm/P1_little_peak.qasm"
number_of_qubits = 4

# Load the circuit from QASM
with open(qasm_path, "r") as f:
    qasm_str = f.read()

# Create a device matching the number of qubits (adjust wires as needed)
dev = qml.device("default.qubit", wires=number_of_qubits,shots=1000)

# Convert QASM string to a PennyLane circuit
circuit = qml.from_qasm(qasm_str)

@qml.qnode(dev)
def run_circuit():
    circuit()
    return qml.probs()

# Run the circuit
state = run_circuit()
print(state)
print(qml.draw(circuit)())
max_index = np.argmax(state)
print(max_index)
print(format(max_index, f'0{number_of_qubits}b'))

[0.007 0.072 0.001 0.007 0.001 0.009 0.    0.    0.07  0.664 0.004 0.062
 0.006 0.086 0.002 0.009]
0: ──RY(2.51)───────────┤  
1: ──X─────────RY(2.51)─┤  
2: ──X─────────RY(2.51)─┤  
3: ──RY(2.51)───────────┤  
9
1001


# Solving Problem 2 : swift rise (28 qubits circuit)

Already, we noticed some limitation with pennylane's default simulator, their tensor network simulator, their lightning simulation, and their gpu-based simulator which require extension configuration. We decided to use the bluequbit plugin made for pennylane in order to easily simulate more qubits.

Security is important ! Never push your token on github, create a .env instead !

In [4]:

load_dotenv() 

token = os.getenv("TOKEN")

In [5]:
# --- Config ---
qasm_path = "circuit_qasm/P2_swift_rise.qasm"
number_of_qubits = 28
shots = 1000
json_path = "resultsP2.json"

# --- Load QASM ---
with open(qasm_path, "r") as f:
    qasm_str = f.read()

# --- Setup Device and Circuit ---
dev = qml.device("bluequbit.cpu", wires=number_of_qubits, token=token, shots=shots)
circuit = qml.from_qasm(qasm_str)

@qml.qnode(dev)
def run_circuit():
    circuit()
    return qml.sample()

# --- Run the Circuit ---
state = run_circuit()
print(state)
print(qml.draw(circuit)())

# --- Convert Samples to Bitstrings ---
bitstrings = ["".join(map(str, s)) for s in state]  # Each sample to string
bitstring_counts = Counter(bitstrings)

# --- Update resultsP2.json ---
# Load old data if exists
if os.path.exists(json_path):
    with open(json_path, "r") as f:
        old_counts = json.load(f)
else:
    old_counts = {}

# Merge new counts
for k, v in bitstring_counts.items():
    old_counts[k] = old_counts.get(k, 0) + v

# Save updated results
with open(json_path, "w") as f:
    json.dump(old_counts, f, indent=4)

print("✅ All results saved and updated.")


[BQ-PYTHON-SDK][WARNING] - Beta version 0.12.0b1 of BlueQubit Python SDK is being used.


[BQ-PYTHON-SDK][INFO] - Submitted: Job ID: fyc6HUZfyRqbpL7r, device: pennylane.cpu, run status: PENDING, created on: 2025-04-13 09:04:44 UTC, estimated runtime: 116300 ms, estimated cost: $0.00, num qubits: 28
Job ID: fyc6HUZfyRqbpL7r, device: pennylane.cpu, run status: COMPLETED, created on: 2025-04-13 09:04:44 UTC, cost: $0.00, run time: 82366 ms, queue time: 87567 ms, num qubits: 28
[[0 0 0 ... 1 0 1]
 [1 1 0 ... 1 0 0]
 [1 1 0 ... 1 0 0]
 ...
 [1 1 0 ... 1 0 0]
 [1 1 0 ... 1 0 0]
 [1 1 0 ... 1 0 0]]
 0: ──RZ(-0.48)──SX──RZ(-1.05)──SX──RZ(-2.62)─╭Z──RZ(-1.56)──SX──RZ(-1.49)──SX──RZ(2.69)─────╭●
 1: ──RZ(-0.93)──SX──RZ(-0.39)──SX──RZ(2.32)──╰●──RZ(-0.35)──SX──RZ(-2.86)──SX──RZ(-0.50)─╭Z─│─
 2: ──RZ(-1.50)──SX──RZ(-2.24)──SX──RZ(-1.20)─╭Z──RZ(1.67)───SX──RZ(-1.50)──SX──RZ(-2.07)─╰●─│─
 3: ──RZ(3.05)───SX──RZ(-0.79)──SX──RZ(1.08)──╰●──RZ(0.56)───SX──RZ(-1.34)──SX──RZ(-1.79)─╭Z─│─
 4: ──RZ(2.23)───SX──RZ(-1.81)──SX──RZ(-2.12)─╭Z──RZ(0.08)───SX──RZ(-0.98)──SX──RZ(0.49)──╰●─│─
 5: ──RZ(1.

We created some function to help us save our shots so that we can decide to account for past result for better analysis. We don't want to run code that take forever to run multiple times for nothing. The following is just helper function to make it so each run, we get more and more measurements on the circuit we are studying.

In [6]:
json_path = "resultsP2.json"

# Load the JSON data
with open(json_path, "r") as f:
    result_counts = json.load(f)

# Total number of samples
total_counts = sum(result_counts.values())

# Sort by frequency (value), descending
sorted_results = sorted(result_counts.items(), key=lambda x: x[1], reverse=True)

# Display top 5 with probability
print("🔝 Top 5 most common bitstrings with probabilities:")
for bitstring, count in sorted_results[:5]:
    probability = count / total_counts
    print(f"{bitstring[::-1]} → {count} times ({probability:.4f} probability)")


🔝 Top 5 most common bitstrings with probabilities:
0011100001101100011011010011 → 1031 times (0.3425 probability)
0011011101101100011011010011 → 13 times (0.0043 probability)
0011100001110111111011010011 → 11 times (0.0037 probability)
0010011101101100011011010011 → 10 times (0.0033 probability)
0011100001101111110011010011 → 10 times (0.0033 probability)


From all of this, we can see that 0011100001101100011011010011 is where the peak is at. Note that pennylane bitstring convention is the reverse of qiskit hence why the ::-1 .

# Solving problem 3 : sharp peak (44 qubits)
Now we are beginning to enter hard-to-simulate territory, using the pennylane plugin isn't enough anymore as we cannot use more than 33 qubits using this plugin. Furthermore, the plugin does not support option to run bluequbit's mps device ! (Hi bluequbit's people, please add options in the device's constructor to allow to use mps in pennylane !)

In [7]:
# --- Config ---
qasm_path = "circuit_qasm/P3__sharp_peak.qasm"
number_of_qubits = 44
shots = 1000
json_path = "resultsP3.json"

# --- Load QASM ---
with open(qasm_path, "r") as f:
    qasm_str = f.read()

# --- Setup Device and Circuit ---
dev = qml.device("bluequbit.cpu", wires=number_of_qubits, token=token, shots=shots)
circuit = qml.from_qasm(qasm_str)

@qml.qnode(dev)
def run_circuit():
    circuit()
    return qml.sample()

# --- Run the Circuit ---
state = run_circuit()
print(state)
print(qml.draw(circuit)())

# --- Convert Samples to Bitstrings ---
bitstrings = ["".join(map(str, s)) for s in state]  # Each sample to string
bitstring_counts = Counter(bitstrings)

# --- Update resultsP2.json ---
# Load old data if exists
if os.path.exists(json_path):
    with open(json_path, "r") as f:
        old_counts = json.load(f)
else:
    old_counts = {}

# Merge new counts
for k, v in bitstring_counts.items():
    old_counts[k] = old_counts.get(k, 0) + v

# Save updated results
with open(json_path, "w") as f:
    json.dump(old_counts, f, indent=4)

print("✅ All results saved and updated.")


[BQ-PYTHON-SDK][WARNING] - Beta version 0.12.0b1 of BlueQubit Python SDK is being used.


BQJobNotCompleteError: Job yJlvwIksJp9C2oHn finished with status: FAILED_VALIDATION. Circuit contains more than 33 qubits, which is not supported for CPU backend with Pennylane. See https://app.bluequbit.io/docs for more details.

## Switching to qiskit

Alright! that's enough of pennylane, lets try loading and simulating our circuit using the qiskit framework instead! We can even use the mps.cpu option here for faster simulation!
Again, all we are doing here is loading the sharp_peak.qasm into our framework, qiskit in this case, and then getting the probability distribution.

In [8]:
from qiskit.visualization import plot_histogram
from qiskit import transpile
from qiskit import qasm2
from qiskit import transpile
from qiskit_addon_cutting import cut_wires, expand_observables
from qiskit_addon_cutting.automated_cut_finding import (
    find_cuts,
    OptimizationParameters,
    DeviceConstraints,
)
from qiskit_addon_cutting import partition_problem
from qiskit_addon_cutting import generate_cutting_experiments
from qiskit_addon_cutting import reconstruct_expectation_values
from qiskit.result import QuasiDistribution
from qiskit.quantum_info import SparsePauliOp

In [9]:
# --- Config ---
qasm_path = "circuit_qasm/P3__sharp_peak.qasm"
json_path = "resultsP3.json"
shots = 1000
device = "mps.cpu"  # or "cpu", "gpu", "quantum"

# --- Init BlueQubit ---
bq = bluequbit.init(token)

# --- Load QASM ---
circuit = qasm2.load(qasm_path)

# Ensure measurement if not present
if not circuit.cregs:
    circuit.measure_all()

# --- Run on BlueQubit ---
results = bq.run(
    circuits=circuit,
    device=device,
    shots=shots,
    asynchronous=False,
    job_name="sharp-peak-qasm"
    )

counts = results.get_counts()

# --- Output ---

# Save to JSON
with open(json_path, "w") as f:
    json.dump(counts, f, indent=2)

if os.path.exists(json_path):
    with open(json_path, "r") as f:
        old_counts = json.load(f)
else:
    old_counts = {}

# Merge new counts
for k, v in counts.items():
    old_counts[k] = old_counts.get(k, 0) + v

# Save updated results
with open(json_path, "w") as f:
    json.dump(old_counts, f, indent=4)

print("✅ All results saved and updated.")

with open(json_path, "r") as f:
    result_counts = json.load(f)

# Total number of samples
total_counts = sum(result_counts.values())

# Sort by frequency (value), descending
sorted_results = sorted(result_counts.items(), key=lambda x: x[1], reverse=True)

# Display top 5 with probability
print("🔝 Top 5 most common bitstrings with probabilities:")
for bitstring, count in sorted_results[:5]:
    probability = count / total_counts
    print(f"{bitstring} → {count} times ({probability:.4f} probability)")



[BQ-PYTHON-SDK][WARNING] - Beta version 0.12.0b1 of BlueQubit Python SDK is being used.


[BQ-PYTHON-SDK][INFO] - Submitted: Job ID: 6T7OeFhnrOEvX8PK, name: sharp-peak-qasm, device: mps.cpu, run status: RUNNING, created on: 2025-04-13 09:09:06 UTC, estimated runtime: 100 ms, estimated cost: $0.00, num qubits: 44
✅ All results saved and updated.
🔝 Top 5 most common bitstrings with probabilities:
10001101010101010000011111001101000100011010 → 238 times (0.1190 probability)
10001101010100100000011111001101000100011010 → 50 times (0.0250 probability)
10001101010101010001101111001101000100011010 → 18 times (0.0090 probability)
10000111010101010000011111001101000100011010 → 14 times (0.0070 probability)
10001101010101010000011111001100010100011010 → 14 times (0.0070 probability)


This is a 44 qubits system, and it worked ! amazing

# Solving problem 4 : Golden mountain
This is where it actually begin to be difficult. we quickly realised that we cannot just simulate it anymore. we have to do something clever, lets look at the circuit, and see how it looks like...

In [3]:
# Path to your QASM file
qasm_path = "circuit_qasm/P4_golden_mountain.qasm"
number_of_qubits = 44
# Load the circuit from QASM
with open(qasm_path, "r") as f:
    qasm_str = f.read()

# Create a device matching the number of qubits (adjust wires as needed)
dev = qml.device("default.qubit", wires=number_of_qubits,shots=1000)

# Convert QASM string to a PennyLane circuit
circuit = qml.from_qasm(qasm_str)

@qml.qnode(dev)
def run_circuit():
    circuit()
    return qml.probs()

print(qml.draw(circuit)())


 0: ──U3(2.01,-0.88,1.80)──╭●──U3(2.47,0.00,-1.57)─╭●──U3(0.10,2.42,-3.11)─────────────────────────
 1: ──U3(1.10,2.52,-2.25)──╰Z──U3(0.90,0.00,1.57)──╰Z──U3(2.08,-0.24,-0.55)─╭●──U3(3.00,0.00,-1.57)
 2: ──U3(2.01,-1.19,2.94)──╭●──U3(3.05,0.00,-1.57)─╭●──U3(0.20,-0.78,-2.27)─╰Z──U3(1.19,0.00,1.57)─
 3: ──U3(1.56,3.04,-1.80)──╰Z──U3(0.13,0.00,1.57)──╰Z──U3(1.64,0.60,-2.05)──╭●──U3(3.00,0.00,-1.57)
 4: ──U3(1.45,2.52,-0.71)──╭●──U3(2.97,0.00,-1.57)─╭●──U3(1.54,2.33,2.10)───╰Z──U3(1.07,0.00,1.57)─
 5: ──U3(0.93,-1.19,-2.51)─╰Z──U3(1.45,0.00,1.57)──╰Z──U3(1.01,-2.99,1.45)──╭●──U3(3.03,0.00,-1.57)
 6: ──U3(3.08,-0.51,-1.25)─╭●──U3(1.97,0.00,-1.57)─╭●──U3(2.18,-2.30,1.94)──╰Z──U3(0.55,0.00,1.57)─
 7: ──U3(0.00,2.13,2.19)───╰Z──U3(1.27,0.00,1.57)──╰Z──U3(1.59,-0.33,-2.22)─╭●──U3(2.17,0.00,-1.57)
 8: ──U3(1.26,-1.51,-0.67)─╭●──U3(2.09,0.00,-1.57)─╭●──U3(1.41,-1.73,2.58)──╰Z──U3(1.30,0.00,1.57)─
 9: ──U3(0.10,-3.03,1.97)──╰Z──U3(1.46,0.00,1.57)──╰Z──U3(1.86,-0.56,2.47)──╭●──U3(3.13,0.00,-1.57)


In [10]:
# --- Config ---
qasm_path = "circuit_qasm/P4_golden_mountain.qasm"
json_path = "resultsP4.json"
shots = 1000
device = "mps.cpu"  # or "cpu", "gpu", "quantum"

# --- Init BlueQubit ---
bq = bluequbit.init(token)

# --- Load QASM ---
circuit = qasm2.load(qasm_path)
print("--- Original Circuit ---")
print(f"Depth: {circuit.depth()}")
print("Gate Counts:")
print(circuit.count_ops())
# to keep CZ gates, you could add basis_gates=['u', 'cz'].
print("\nOptimizing with optimization_level=3...")
# For complex circuits and high optimization, this can take some time
circuit = transpile(circuit, optimization_level=3)
print("\n--- Optimized Circuit ---")
print(f"Depth: {circuit.depth()}")
# print(f"Size: {optimized_circuit.size()}")
print("Gate Counts:")
print(circuit.count_ops())
# Ensure measurement if not present
if not circuit.cregs:
    circuit.measure_all()

print(circuit.draw(output='text'))
# --- Run on BlueQubit ---
results = bq.run(
    circuits=circuit,
    device=device,
    shots=shots,
    asynchronous=False,
    job_name="sharp-peak-qasm",
    options={'mps_bond_dimension':128,'mps_truncation_threshold':1e-16}
    )

# --- Get Results ---
counts = results.get_counts()
# --- Output ---

# Save to JSON
with open(json_path, "w") as f:
    json.dump(counts, f, indent=2)

if os.path.exists(json_path):
    with open(json_path, "r") as f:
        old_counts = json.load(f)
else:
    old_counts = {}

# Merge new counts
for k, v in counts.items():
    old_counts[k] = old_counts.get(k, 0) + v

# Save updated results
with open(json_path, "w") as f:
    json.dump(old_counts, f, indent=4)

print("✅ All results saved and updated.")

with open(json_path, "r") as f:
    result_counts = json.load(f)

# Total number of samples
total_counts = sum(result_counts.values())

# Sort by frequency (value), descending
sorted_results = sorted(result_counts.items(), key=lambda x: x[1], reverse=True)

# Display top 5 with probability
print("🔝 Top 5 most common bitstrings with probabilities:")
for bitstring, count in sorted_results[:5]:
    probability = count / total_counts
    print(f"{bitstring[::-1]} → {count} times ({probability:.4f} probability)")

[BQ-PYTHON-SDK][WARNING] - Beta version 0.12.0b1 of BlueQubit Python SDK is being used.


--- Original Circuit ---
Depth: 437
Gate Counts:
OrderedDict({'u3': 10240, 'cz': 5096})

Optimizing with optimization_level=3...

--- Optimized Circuit ---
Depth: 437
Gate Counts:
OrderedDict({'u3': 10240, 'cz': 5096})
           ┌────────────────────────────┐    ┌───────────────────┐   »
    q_0: ──┤ U3(2.0058,-0.88174,1.7983) ├──■─┤ U3(2.4726,0,-π/2) ├─■─»
           ├───────────────────────────┬┘  │ ├───────────────────┤ │ »
    q_1: ──┤ U3(1.0968,2.5238,-2.2517) ├───■─┤ U3(0.89549,0,π/2) ├─■─»
           └┬──────────────────────────┤     ├───────────────────┤   »
    q_2: ───┤ U3(2.0069,-1.1891,2.942) ├───■─┤ U3(3.0502,0,-π/2) ├─■─»
           ┌┴──────────────────────────┤   │ ├───────────────────┤ │ »
    q_3: ──┤ U3(1.5622,3.0437,-1.7951) ├───■─┤ U3(0.13117,0,π/2) ├─■─»
           ├───────────────────────────┴┐    ├───────────────────┤   »
    q_4: ──┤ U3(1.4531,2.5221,-0.71398) ├──■─┤ U3(2.9712,0,-π/2) ├─■─»
          ┌┴────────────────────────────┤  │ └┬─────────────────┬┘ │ »


BQJobNotCompleteError: Job zjPOaeaYFuUhAoKn finished with status: FAILED_VALIDATION. The number of two-qubit gates is too big for mps.cpu (maximum 1000). See https://app.bluequbit.io/docs for more details.

Ummm... too many 2 qubit gates... lets count how many

In [11]:
two_qubit_gates = [gate for gate, qargs, _ in circuit.data if len(qargs) == 2]
print("Number of 2-qubit gates:", len(two_qubit_gates))

Number of 2-qubit gates: 5096


C:\Users\Kuift\AppData\Local\Temp\ipykernel_16088\3617306113.py:1: DeprecationWarning: Treating CircuitInstruction as an iterable is deprecated legacy behavior since Qiskit 1.2, and will be removed in Qiskit 2.0. Instead, use the `operation`, `qubits` and `clbits` named attributes.
  two_qubit_gates = [gate for gate, qargs, _ in circuit.data if len(qargs) == 2]


5096 ! holy, we need to find another way.

# Enter circuit cutting
We need to simulate smaller circuits, but circuit cutting can actually increase the number of gate/depth. We have to be smart about it.

In [12]:
load_dotenv() 

token = os.getenv("TOKEN")

# Specify settings for the cut-finding optimizer
optimization_settings = OptimizationParameters(seed=111)

# --- Config ---
qasm_path = "circuit_qasm/P4_golden_mountain.qasm"
json_path = "resultsP4.json"
shots = 10
device = "mps.cpu" 
# --- Init BlueQubit ---
bq = bluequbit.init(token)

# --- Load QASM ---
circuit = qasm2.load(qasm_path)


[BQ-PYTHON-SDK][WARNING] - Beta version 0.12.0b1 of BlueQubit Python SDK is being used.


### A key point here!
We put the subcircuit to be a multiple of the circuit we are analyzing ie we have a quantum circuit with 48 qubits, which is divisible by 1, 2, 3, 4, 6, 8, 12, 16, 24 and 48.
we ended up choosing 8 because it was an option that could run on bluequbit's mps.cpu backend. 

In [13]:
# Specify the size of the QPUs available
device_constraints = DeviceConstraints(qubits_per_subcircuit=8)

cut_circuit, metadata = find_cuts(circuit, optimization_settings, device_constraints)
print(f"cuts found :{cut_circuit} metadata :{metadata}")

c:\Users\Kuift\AppData\Local\Programs\Python\Python312\Lib\site-packages\qiskit_addon_cutting\automated_cut_finding.py:134: RuntimeWarning: overflow encountered in scalar power
  metadata["sampling_overhead"] = opt_out.upper_bound_gamma() ** 2


cuts found :        ┌────────────────────────────┐    ┌───────────────────┐   »
 q_0: ──┤ U3(2.0058,-0.88174,1.7983) ├──■─┤ U3(2.4726,0,-π/2) ├─■─»
        ├───────────────────────────┬┘  │ ├───────────────────┤ │ »
 q_1: ──┤ U3(1.0968,2.5238,-2.2517) ├───■─┤ U3(0.89549,0,π/2) ├─■─»
        └┬──────────────────────────┤     ├───────────────────┤   »
 q_2: ───┤ U3(2.0069,-1.1891,2.942) ├───■─┤ U3(3.0502,0,-π/2) ├─■─»
        ┌┴──────────────────────────┤   │ ├───────────────────┤ │ »
 q_3: ──┤ U3(1.5622,3.0437,-1.7951) ├───■─┤ U3(0.13117,0,π/2) ├─■─»
        ├───────────────────────────┴┐    ├───────────────────┤   »
 q_4: ──┤ U3(1.4531,2.5221,-0.71398) ├──■─┤ U3(2.9712,0,-π/2) ├─■─»
       ┌┴────────────────────────────┤  │ └┬─────────────────┬┘ │ »
 q_5: ─┤ U3(0.92899,-1.1869,-2.5086) ├──■──┤ U3(1.452,0,π/2) ├──■─»
       ├─────────────────────────────┤    ┌┴─────────────────┴┐   »
 q_6: ─┤ U3(3.0786,-0.50604,-1.2483) ├──■─┤ U3(1.9707,0,-π/2) ├─■─»
       ├────────────────────────────

In [14]:
qc_w_ancilla = cut_wires(cut_circuit)
print(f'qc ancilla : {qc_w_ancilla}')

qc ancilla :         ┌────────────────────────────┐    ┌───────────────────┐   »
 q_0: ──┤ U3(2.0058,-0.88174,1.7983) ├──■─┤ U3(2.4726,0,-π/2) ├─■─»
        ├───────────────────────────┬┘  │ ├───────────────────┤ │ »
 q_1: ──┤ U3(1.0968,2.5238,-2.2517) ├───■─┤ U3(0.89549,0,π/2) ├─■─»
        └┬──────────────────────────┤     ├───────────────────┤   »
 q_2: ───┤ U3(2.0069,-1.1891,2.942) ├───■─┤ U3(3.0502,0,-π/2) ├─■─»
        ┌┴──────────────────────────┤   │ ├───────────────────┤ │ »
 q_3: ──┤ U3(1.5622,3.0437,-1.7951) ├───■─┤ U3(0.13117,0,π/2) ├─■─»
        ├───────────────────────────┴┐    ├───────────────────┤   »
 q_4: ──┤ U3(1.4531,2.5221,-0.71398) ├──■─┤ U3(2.9712,0,-π/2) ├─■─»
       ┌┴────────────────────────────┤  │ └┬─────────────────┬┘ │ »
 q_5: ─┤ U3(0.92899,-1.1869,-2.5086) ├──■──┤ U3(1.452,0,π/2) ├──■─»
       ├─────────────────────────────┤    ┌┴─────────────────┴┐   »
 q_6: ─┤ U3(3.0786,-0.50604,-1.2483) ├──■─┤ U3(1.9707,0,-π/2) ├─■─»
       ├───────────────────────────

In [15]:
observable = SparsePauliOp(["Z" + "I"*46 + "Z"])
observables_expanded = expand_observables(observable.paulis, circuit, qc_w_ancilla)
print(observables_expanded)

['ZIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIZ']


In [16]:
partitioned_problem = partition_problem(circuit=qc_w_ancilla, observables=observables_expanded)
partitioned_problem


PartitionedCuttingProblem(subcircuits={0: <qiskit.circuit.quantumcircuit.QuantumCircuit object at 0x00000137B89AB5F0>, 1: <qiskit.circuit.quantumcircuit.QuantumCircuit object at 0x00000137B9840980>, 2: <qiskit.circuit.quantumcircuit.QuantumCircuit object at 0x000001388731C7A0>, 3: <qiskit.circuit.quantumcircuit.QuantumCircuit object at 0x00000137B83209E0>, 4: <qiskit.circuit.quantumcircuit.QuantumCircuit object at 0x00000137B9798EC0>, 5: <qiskit.circuit.quantumcircuit.QuantumCircuit object at 0x00000137B98553A0>}, bases=[<qiskit_addon_cutting.qpd.qpd_basis.QPDBasis object at 0x0000013887569700>, <qiskit_addon_cutting.qpd.qpd_basis.QPDBasis object at 0x00000138875697C0>, <qiskit_addon_cutting.qpd.qpd_basis.QPDBasis object at 0x0000013887569910>, <qiskit_addon_cutting.qpd.qpd_basis.QPDBasis object at 0x0000013887569A60>, <qiskit_addon_cutting.qpd.qpd_basis.QPDBasis object at 0x0000013887569BB0>, <qiskit_addon_cutting.qpd.qpd_basis.QPDBasis object at 0x0000013887569D00>, <qiskit_addon_cut

In [17]:
subcircuits = partitioned_problem.subcircuits
subcircuits

{0: <qiskit.circuit.quantumcircuit.QuantumCircuit at 0x137b89ab5f0>,
 1: <qiskit.circuit.quantumcircuit.QuantumCircuit at 0x137b9840980>,
 2: <qiskit.circuit.quantumcircuit.QuantumCircuit at 0x1388731c7a0>,
 3: <qiskit.circuit.quantumcircuit.QuantumCircuit at 0x137b83209e0>,
 4: <qiskit.circuit.quantumcircuit.QuantumCircuit at 0x137b9798ec0>,
 5: <qiskit.circuit.quantumcircuit.QuantumCircuit at 0x137b98553a0>}

In [18]:
subobservables = partitioned_problem.subobservables
subobservables

{0: PauliList(['IIIIIIIZ']),
 1: PauliList(['IIIIIIII']),
 2: PauliList(['IIIIIIII']),
 3: PauliList(['IIIIIIII']),
 4: PauliList(['IIIIIIII']),
 5: PauliList(['ZIIIIIII'])}

In [20]:
subexperiments, coefficients = generate_cutting_experiments(circuits=subcircuits,observables=subobservables,num_samples=10)

print(f"Generated {len(coefficients)} coefficients.")

for key, S_k in subexperiments.items():
    print(f"Subsystem '{key}':")
    print(f"  Num generated experiments: {len(S_k)}")
    num_groups_inferred = 1 
    expected_experiments = len(coefficients) * num_groups_inferred
    print(f"  Expected experiments (based on {len(coefficients)} coeffs and {num_groups_inferred} inferred group(s)): {expected_experiments}")

    if len(S_k) != expected_experiments:
        print(f"  --> MISMATCH DETECTED for subsystem '{key}' (Expected {expected_experiments}, Got {len(S_k)})")
    else:
        print(f"  --> Lengths match for subsystem '{key}'")

Generated 10 coefficients.
Subsystem '0':
  Num generated experiments: 10
  Expected experiments (based on 10 coeffs and 1 inferred group(s)): 10
  --> Lengths match for subsystem '0'
Subsystem '1':
  Num generated experiments: 10
  Expected experiments (based on 10 coeffs and 1 inferred group(s)): 10
  --> Lengths match for subsystem '1'
Subsystem '2':
  Num generated experiments: 10
  Expected experiments (based on 10 coeffs and 1 inferred group(s)): 10
  --> Lengths match for subsystem '2'
Subsystem '3':
  Num generated experiments: 10
  Expected experiments (based on 10 coeffs and 1 inferred group(s)): 10
  --> Lengths match for subsystem '3'
Subsystem '4':
  Num generated experiments: 10
  Expected experiments (based on 10 coeffs and 1 inferred group(s)): 10
  --> Lengths match for subsystem '4'
Subsystem '5':
  Num generated experiments: 10
  Expected experiments (based on 10 coeffs and 1 inferred group(s)): 10
  --> Lengths match for subsystem '5'


In [ ]:
from qiskit_aer import AerSimulator
from qiskit_ibm_runtime import SamplerV2, Batch

backend = AerSimulator(method='matrix_product_state')

from qiskit.transpiler import generate_preset_pass_manager

# Transpile the subexperiments to ISA circuits
pass_manager = generate_preset_pass_manager(optimization_level=1, backend=backend)
isa_subexperiments = {
    label: pass_manager.run(partition_subexpts)
    for label, partition_subexpts in subexperiments.items()
}

# all_counts = {}
# for key, group in subexperiments.items():
#     counts_per_group = []
#     for i, value in enumerate(group):

with Batch(backend=backend) as batch:
    sampler = SamplerV2(mode=batch)
    jobs = {
        label: sampler.run(subsystem_subexpts, shots=2**12)
        for label, subsystem_subexpts in isa_subexperiments.items()
    }
results = {label: job.result() for label, job in jobs.items()}

        # print(f"Running subcircuit {i} with {len(value)} gates, circuits, size : {value.num_qubits}")
        # results = simulator.run(#bq.run(
        #     circuits=value,
        #     #device=device,
        #     shots=shots,
        #     #asynchronous=False,
        #     #job_name=f"synced-cut-subcircuit-group-{key}-{i}",
        #     #options={'mps_bond_dimension':128, 'mps_truncation_threshold':1e-16}
        # ).result()
        # counts_per_group.append(results)
    # all_counts[key] = counts_per_group 


In [31]:
# Reconstructing the expectation values of our 48 qubits circuit
reconstructed_expval_terms = reconstruct_expectation_values(
    all_counts,
    coefficients,
    subobservables,
)

# Reconstruct final expectation value
reconstructed_expval = np.dot(reconstructed_expval_terms, observable.coeffs)
print(f"Reconstructed expectation value: {reconstructed_expval}")

AttributeError: 'function' object has no attribute 'observable_measurements'

In [79]:
counts = all_counts
for i in counts:
    print(i)
# Save to JSON
with open(json_path, "w") as f:
    json.dump(counts, f, indent=2)

if os.path.exists(json_path):
    with open(json_path, "r") as f:
        old_counts = json.load(f)
else:
    old_counts = {}

# Merge new counts
for k, v in counts.items():
    old_counts[k] = old_counts.get(k, 0) + v

# Save updated results
with open(json_path, "w") as f:
    json.dump(old_counts, f, indent=4)

print("✅ All results saved and updated.")

with open(json_path, "r") as f:
    result_counts = json.load(f)

# Total number of samples
total_counts = sum(result_counts.values())

# Sort by frequency (value), descending
sorted_results = sorted(result_counts.items(), key=lambda x: x[1], reverse=True)

# Display top 5 with probability
print("🔝 Top 5 most common bitstrings with probabilities:")
for bitstring, count in sorted_results[:5]:
    probability = count / total_counts
    print(f"{bitstring} → {count} times ({probability:.4f} probability)")

{'00001100': 1, '00110000': 1, '01001011': 1, '01010110': 1, '01011010': 1, '01110000': 1, '10001000': 1, '10011101': 1, '11010001': 1, '11100111': 1}
{'00010011': 1, '01010011': 1, '10011100': 1, '10111100': 1, '11001000': 1, '11001101': 1, '11011000': 2, '11100000': 1, '11100010': 1}
{'00001110': 1, '00101111': 1, '00110111': 1, '00111010': 1, '00111100': 1, '10000011': 1, '10010001': 1, '10011011': 1, '10011110': 1, '10100010': 1}
{'00010100': 2, '00111011': 1, '01000100': 1, '01010111': 1, '01101000': 1, '01111101': 1, '11000100': 1, '11100101': 1, '11111101': 1}
{'00000111': 1, '00001101': 1, '00011010': 1, '00101001': 2, '00101010': 1, '01100001': 1, '01100111': 1, '10011100': 1, '10111110': 1}
{'00001100': 1, '00011010': 1, '00111000': 1, '01000101': 1, '01100111': 1, '01110000': 1, '10001010': 1, '10011000': 1, '10110010': 1, '11110100': 1}
{'00011110': 1, '00100110': 1, '00100111': 1, '00110100': 1, '01111001': 1, '10010101': 2, '10011000': 1, '10011110': 1, '11100110': 1}
{'0

AttributeError: 'list' object has no attribute 'items'